## Предобработка данных

In [67]:
import numpy as np
import pandas as pd

In [68]:
# Загрузим набор данных

df = pd.read_csv('freMPL-R.csv', low_memory=False)
df = df.loc[df.Dataset.isin([5, 6, 7, 8, 9])]
df.drop('Dataset', axis=1, inplace=True)
df.dropna(axis=1, how='all', inplace=True)
df.drop_duplicates(inplace=True)
df.reset_index(drop=True, inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 115155 entries, 0 to 115154
Data columns (total 20 columns):
Exposure             115155 non-null float64
LicAge               115155 non-null int64
RecordBeg            115155 non-null object
RecordEnd            59455 non-null object
Gender               115155 non-null object
MariStat             115155 non-null object
SocioCateg           115155 non-null object
VehUsage             115155 non-null object
DrivAge              115155 non-null int64
HasKmLimit           115155 non-null int64
BonusMalus           115155 non-null int64
ClaimAmount          115155 non-null float64
ClaimInd             115155 non-null int64
ClaimNbResp          115155 non-null float64
ClaimNbNonResp       115155 non-null float64
ClaimNbParking       115155 non-null float64
ClaimNbFireTheft     115155 non-null float64
ClaimNbWindscreen    115155 non-null float64
OutUseNb             115155 non-null float64
RiskArea             115155 non-null float64
dtypes

В предыдущем уроке мы заметили отрицательную величину убытка для некоторых наблюдений. Заметим, что для всех таких полисов переменная "ClaimInd" принимает только значение 0. Поэтому заменим все соответствующие значения "ClaimAmount" нулями.

In [69]:
NegClaimAmount = df.loc[df.ClaimAmount < 0, ['ClaimAmount','ClaimInd']]
print('Unique values of ClaimInd:', NegClaimAmount.ClaimInd.unique())
NegClaimAmount.head()

Unique values of ClaimInd: [0]


ClaimAmount  ClaimInd
82    -74.206042         0
175 -1222.585196         0
177  -316.288822         0
363  -666.758610         0
375 -1201.600604         0

In [70]:
df.loc[df.ClaimAmount < 0, 'ClaimAmount'] = 0

Перекодируем переменные типа `object` с помощью числовых значений

In [71]:
def SeriesFactorizer(series):
    series, unique = pd.factorize(series)
    reference = {x: i for x, i in enumerate(unique)}
    print(reference)
    return series, reference

In [72]:
df.Gender, GenderRef = SeriesFactorizer(df.Gender)

{0: 'Male', 1: 'Female'}


In [73]:
df.MariStat, MariStatRef = SeriesFactorizer(df.MariStat)

{0: 'Other', 1: 'Alone'}


Для переменных, содержащих более 2 значений, различия между которыми не могут упорядочены, используем фиктивные переменные (one-hot encoding).

**NB**: В H2O не рекомендуется использовать one-hot encoding, поскольку данный фреймворк корректно работает с категориальными признаками, тогда как применение one-hot encoding приводит к неэффективности. Тем не менее, используем здесь фиктивные переменные, чтобы в дальнейшем сохранить возможность сравнения результатов построенных моделей.

In [74]:
list(df.VehUsage.unique())

['Professional', 'Private+trip to office', 'Private', 'Professional run']

In [75]:
VU_dummies = pd.get_dummies(df.VehUsage, prefix='VehUsg', drop_first=False)
VU_dummies.head()

VehUsg_Private  VehUsg_Private+trip to office  VehUsg_Professional  \
0               0                              0                    1   
1               0                              0                    1   
2               0                              1                    0   
3               0                              1                    0   
4               1                              0                    0   

   VehUsg_Professional run  
0                        0  
1                        0  
2                        0  
3                        0  
4                        0

In [76]:
df = pd.concat([df, VU_dummies], axis=1)

Фактор "SocioCateg" содержит информацию о социальной категории в виде кодов классификации CSP. Агрегируем имеющиеся коды до 1 знака, а затем закодируем их с помощью one-hot encoding.

[Wiki](https://fr.wikipedia.org/wiki/Professions_et_cat%C3%A9gories_socioprofessionnelles_en_France#Cr%C3%A9ation_de_la_nomenclature_des_PCS)

[Более подробный классификатор](https://www.ast74.fr/upload/administratif/liste-des-codes-csp-copie.pdf)

In [77]:
df['SocioCateg'].unique()

array(['CSP50', 'CSP55', 'CSP60', 'CSP48', 'CSP6', 'CSP66', 'CSP1',
       'CSP46', 'CSP21', 'CSP47', 'CSP42', 'CSP37', 'CSP22', 'CSP3',
       'CSP49', 'CSP20', 'CSP2', 'CSP40', 'CSP7', 'CSP26', 'CSP65',
       'CSP41', 'CSP17', 'CSP57', 'CSP56', 'CSP38', 'CSP51', 'CSP59',
       'CSP30', 'CSP44', 'CSP61', 'CSP63', 'CSP45', 'CSP16', 'CSP43',
       'CSP39', 'CSP5', 'CSP32', 'CSP35', 'CSP73', 'CSP62', 'CSP52',
       'CSP27', 'CSP24', 'CSP19', 'CSP70'], dtype=object)

In [78]:
df['SocioCateg'] = df.SocioCateg.str.slice(0,4)

In [79]:
SocCatSize = pd.DataFrame(df.groupby('SocioCateg').size().sort_values(), columns=['Frequency'])
SocCatSize

Frequency
SocioCateg           
CSP7               14
CSP3             1210
CSP1             2740
CSP2             3254
CSP4             7648
CSP6            24833
CSP5            75456

In [80]:
df = pd.concat([df, pd.get_dummies(df.SocioCateg)], axis=1)

Теперь, когда большинство переменных типа `object` обработаны, исключим их из набора данных за ненадобностью.

In [81]:
df = df.select_dtypes(exclude=['object'])

Также создадим такую переменную, как квадрат возраста.

In [82]:
df['DrivAgeSq'] = df.DrivAge.apply(lambda x: x**2)
df.head()

Exposure  LicAge  Gender  MariStat  DrivAge  HasKmLimit  BonusMalus  \
0     0.083     332       0         0       46           0          50   
1     0.916     333       0         0       46           0          50   
2     0.550     173       0         0       32           0          68   
3     0.089     364       1         0       52           0          50   
4     0.233     426       0         0       57           0          50   

   ClaimAmount  ClaimInd  ClaimNbResp  ...  VehUsg_Professional  \
0          0.0         0          0.0  ...                    1   
1          0.0         0          0.0  ...                    1   
2          0.0         0          0.0  ...                    0   
3          0.0         0          0.0  ...                    0   
4          0.0         0          0.0  ...                    0   

   VehUsg_Professional run  CSP1  CSP2  CSP3  CSP4  CSP5  CSP6  CSP7  \
0                        0     0     0     0     0     1     0     0   
1                        0     0     0     0     0     1     0     0   
2                        0     0     0     0     0     1     0     0   
3                        0     0     0     0     0     1     0     0   
4                        0     0     0     0     0     0     1     0   

   DrivAgeSq  
0       2116  
1       2116  
2       1024  
3       2704  
4       3249  

[5 rows x 28 columns]

Для моделирования частоты убытков сгенерируем показатель как сумму индикатора того, что убыток произошел ("ClaimInd") и количества заявленных убытков по различным видам ущерба за 4 предшествующих года ("ClaimNbResp", "ClaimNbNonResp", "ClaimNbParking", "ClaimNbFireTheft", "ClaimNbWindscreen").

В случаях, если соответствующая величина убытка равняется нулю, сгенерированную частоту также обнулим.

In [83]:
df['ClaimsCount'] = df.ClaimInd + df.ClaimNbResp + df.ClaimNbNonResp + df.ClaimNbParking + df.ClaimNbFireTheft + df.ClaimNbWindscreen
df.loc[df.ClaimAmount == 0, 'ClaimsCount'] = 0
df.drop(["ClaimNbResp", "ClaimNbNonResp", "ClaimNbParking", "ClaimNbFireTheft", "ClaimNbWindscreen"], axis=1, inplace=True)

In [84]:
ClaimsCountGroup = pd.DataFrame(df.groupby('ClaimsCount').size(), columns=['Policies'])
ClaimsCountGroup

Policies
ClaimsCount          
0.0            104286
1.0              3339
2.0              3529
3.0              2310
4.0              1101
5.0               428
6.0               127
7.0                26
8.0                 6
9.0                 2
11.0                1

In [85]:
import plotly.express as px
fig = px.scatter(df, x='ClaimsCount', y='ClaimAmount', title='Зависимость между частотой и величиной убытков')
fig.show()

Для моделирования среднего убытка можем рассчитать его как отношение величины убытков к их частоте.

In [86]:
dfAC = df[df.ClaimsCount > 0].copy()
dfAC['AvgClaim'] = dfAC.ClaimAmount/dfAC.ClaimsCount

## Разделение набора данных на обучающую, валидационную и тестовую выборки

In [87]:
from sklearn.model_selection import train_test_split

In [88]:
# Разбиение датасета для частоты на train/val/test

x_train_c, x_test_c, y_train_c, y_test_c = train_test_split(df.drop(['ClaimInd', 'ClaimAmount', 'ClaimsCount'], axis=1), df.ClaimsCount, test_size=0.15, random_state=1)
x_train_c, x_valid_c, y_train_c, y_valid_c = train_test_split(x_train_c, y_train_c, test_size=0.15, random_state=1)

In [89]:
# Разбиение датасета для среднего убытка на train/val/test 

x_train_ac, x_test_ac, y_train_ac, y_test_ac = train_test_split(dfAC.drop(['ClaimInd', 'ClaimAmount', 'ClaimsCount', 'AvgClaim'], axis=1), dfAC.AvgClaim, test_size=0.15, random_state=1)
x_train_ac, x_valid_ac, y_train_ac, y_valid_ac = train_test_split(x_train_ac, y_train_ac, test_size=0.15, random_state=1)

## Обобщенные линейные модели (Generalized Linear Models, GLM)

### Теория

Пусть $y$ – целевая переменная, $X$ – матрица объясняющих переменных, $\beta$ – вектор параметров модели.

Матрица $X$ составлена из всех векторов наблюдений $x_i$, каждый из которых представляет собой объясняющую переменную.

Основные компоненты обобщенной линейной модели:
* Систематическая компонента $\eta$:
    * $\eta = X\beta \hspace{10pt}(=\beta_0+\beta_1x_1+\beta_2x_2+\dots+\beta_nx_n)$.
* Случайная компонента $y$:
    * Элементы вектора $y$ – независимые одинаково распределенные случайные величины, имеющие функцию плотности распределения $f(y;\theta,\phi)$ из экспоненциального семейства.
    * Распределения из экспоненциального семейства имеют параметры $\theta$ (характеристика среднего) и $\phi$ (характеристика дисперсии). В общем виде данные распределения могут быть определены:
    $$f_i(y_i;\theta_i,\phi)=\exp\left\lbrace \frac{y_i\theta_i-b(\theta_i)}{a_i(\phi)} + c(y_i, \phi) \right\rbrace,$$
    где $a_i(\phi)$, $b(\theta_i)$ и $c(y_i, \phi)$ некоторые функции.
    * Для распределений из данного семейства дисперсия является функцией от среднего.
    * Экспоненциальное семейство включает распределения нормальное, экспоненциальное, Пуассона, гамма, хи-квадрат, бета и другие.
* Функция связи $g$:
    * $\mathbb{E}\left[y\right]=\mu=g^{-1}\left(\eta\right)$, $\mu$ – математическое ожидание $y$;
    * $g$ – монотонная дифференцируемая функция.




#### GLM с распределением Пуассона

Регрессия Пуассона обычно используется в случаях, когда зависимая переменная представляет собой счетные значения и ошибки предполагаются распределенными в соответствии с распределением Пуассона. Зависимая переменная должна быть неотрицательной.

Функции связи между таргетом и объясняющими переменными предполагается логарифмической:
$$g(\eta) = \ln(\eta) \Rightarrow \hat {y} = e^{x{^T}\beta + {\beta_{0}}}.$$

Модель оценивается методом максимального правдоподобия, функция логарифма правдоподобия с учетом штрафа регуляризации эластичной сети имеет вид:
$$\max_{\beta,\beta_0} \frac{1}{N} \sum_{i=1}^{N} \Big( y_i(x_{i}^{T}\beta + \beta_0) - e^{x{^T_i}\beta + {\beta_0}} \Big)- \lambda \Big( \alpha||\beta||_1 + \dfrac {1} {2}(1 - \alpha)||\beta||^2_2 \Big),$$

где 
* $\lambda$ – параметр, отвечающий за силу регуляризации. $\lambda\in\mathbb{R}^{+}$;
* $\alpha$ – параметр, отвечающий за распределение штрафов регуляризации между нормой 1 ($\ell_1$) и нормой 2 ($\ell_2$). $\alpha\in[0,1]$;
* $||\beta||{_1}$ – штраф регуляризации $\ell_1$ (LASSO). $||\beta||{_1} = \sum{^p_{k=1}} |\beta{_k}|$;
* $||\beta||{_2}$ – штраф регуляризации $\ell_2$ (Ridge). $||\beta||{_2} = \sum{^p_{k=1}} \beta{^2_k}$.

Тогда соответствующая метрика _Deviance_ имеет вид:
$$D = -2 \sum_{i=1}^{N} \big( y_i \text{ln}(y_i / \hat {y}_i) - (y_i - \hat {y}_i) \big).$$

##### Вывод функции правдоподобия для GLM с распределением Пуассона (без регуляризации)

**NB:** Ниже $\lambda$ не имеет отношения к вышеупомянутому одноименному параметру регуляризации.

Напомним, что функция вероятности для распределения Пуассона имеет вид:
$$p(k;\lambda) = \frac{\lambda^k e^{-\lambda}}{k!}, \hspace{10pt} \lambda\in\mathbb{R}^{+}.$$
Также, для распределения Пуассона справедливо, что:
$$\mathbb{E}\left[k\right] = Var(k) = \lambda.$$
Тогда, для оценивания коэффициентов нашей модели необходимо максимизировать правдоподобие (совместную условную вероятность при имеющихся данных), что данные имеют распределение Пуассона:
$$p(y_1,\dots,y_n|x_1,\dots,x_n;\beta_0,\beta) = \prod_{i=1}^{N}\frac{e^{y_i(x_i{^T}\beta + {\beta_{0}})} e^{-e^{x_i{^T}\beta + {\beta_{0}}}}}{y_i!} = L(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n).$$
Для упрощения задачи оптимизации перейдем к логарифму правдоподобия:
$$\ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n) = \sum_{i=1}^{N}\left(y_i(x_i{^T}\beta + {\beta_{0}}) -e^{x_i{^T}\beta + {\beta_{0}}}-\ln(y_i!)\right).$$
Поскольку величина $\ln(y_i!)$ не зависит от выбора параметров, можно упростить задачу:
$$\ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n) = \sum_{i=1}^{N}\left(y_i(x_i{^T}\beta + {\beta_{0}}) -e^{x_i{^T}\beta + {\beta_{0}}}\right).$$
Далее численно решается задача оптимизации для определения параметров модели:
$$\frac{\partial \ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n)}{\partial \beta_0} = 0,\\\frac{\partial \ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n)}{\partial \beta} = 0.$$
Обычно минимизируется отрицательное правдоподобие, которое является выпуклой функцией.

##### Вывод метрики Deviance для GLM с распределением Пуассона

Метрика Deviance представляет собой отношение правдоподобия между двумя моделями: рассматриваемой моделью и "идеальной" моделью, в которая бы идеально предсказывала бы зависимую переменную.
$$Deviance = 2(\ell_{ideal} - \ell_{model})$$

В качестве такой "идеальной модели" может использоваться сама зависимая переменная. Тогда, логарифм правдоподобия "идеальной модели" для GLM с распределением Пуассона имеет вид:
$$\ell_{ideal} = \sum_{i=1}^{N}\left(y_i \ln(y_i) -y_i-\ln(y_i!)\right).$$

Из приведенного выше вывода правдоподобия для рассматриваемой модели, мы можем записать, обозначив $\hat{y}_i = e^{x{^T}\beta + {\beta_{0}}}$:
$$\ell_{model} = \sum_{i=1}^{N}\left(y_i \ln(\hat{y}_i) -\hat{y}_i-\ln(y_i!)\right).$$

Тогда получаем,
$$Deviance = 2\sum_{i=1}^{N}\left(y_i \ln(y_i) -y_i - y_i \ln(\hat{y}_i) +\hat{y}_i\right) = -2\sum_{i=1}^{N}\left(y_i \ln(y_i/\hat{y}_i) - (y_i -\hat{y}_i)\right).$$


#### GLM с гамма-распределением

GLM с гамма-распределением используется для моделирования положительной непрерывной зависимой переменной, когда ее условная дисперсия увеличивается вместе со средним значением, но коэффициент вариации зависимой переменной предполагается постоянным.

Обычно GLM с гамма-распределением используются с логарифмической или обратной функциями связи:
$$g(\eta) = \ln(\eta);\hspace{20pt}g(\eta) = \frac{1}{\eta}.$$

Модель оценивается методом максимального правдоподобия, функция логарифма правдоподобия (для обратной функции связи) с учетом штрафа регуляризации эластичной сети имеет вид:
$$\max_{\beta,\beta_0} - \frac{1}{N} \sum_{i=1}^{N} \frac{y_i}{x{^T_i}\beta + \beta_0} + \text{ln} \big( x{^T_i}\beta + \beta_0 \big ) - \lambda \Big( \alpha||\beta||_1 + \dfrac {1} {2}(1 - \alpha)||\beta||^2_2 \Big),$$

где 
* $\lambda$ – параметр, отвечающий за силу регуляризации. $\lambda\in\mathbb{R}^{+}$;
* $\alpha$ – параметр, отвечающий за распределение штрафов регуляризации между нормой 1 ($\ell_1$) и нормой 2 ($\ell_2$). $\alpha\in[0,1]$;
* $||\beta||{_1}$ – штраф регуляризации $\ell_1$ (LASSO). $||\beta||{_1} = \sum{^p_{k=1}} |\beta{_k}|$;
* $||\beta||{_2}$ – штраф регуляризации $\ell_2$ (Ridge). $||\beta||{_2} = \sum{^p_{k=1}} \beta{^2_k}$.

Соответствующая метрика _Deviance_ имеет вид:
$$D = 2 \sum_{i=1}^{N} - \text{ln} \bigg (\dfrac {y_i} {\hat {y}_i} \bigg) + \dfrac {(y_i - \hat{y}_i)} {\hat {y}_i}.$$




##### Вывод функции правдоподобия для GLM с Гамма-распределением и логарифмической функцией связи (без регуляризации)

**NB:** Ниже $\alpha$ и $\lambda$ не имеют отношения к вышеупомянутым одноименным параметрам регуляризации.

Напомним, что функция плотности вероятности для Гамма-распределения имеет вид:
$$f(x;\alpha,\lambda) = 
\begin{cases}
\frac{\alpha^\lambda}{\Gamma(\lambda)}x^{\lambda-1}e^{-\alpha x},&x \ge 0\\
0,& x <0
\end{cases},\hspace{20pt} \Gamma(x) = \int_0^{\infty}x^{\lambda-1}e^{-x}dx.
$$
Также, для Гамма-распределения справедливо, что:
$$ \mathbb{E}[x] = \frac{\lambda}{\alpha},\hspace{15pt} Var(x) = \frac{\lambda}{\alpha^2}.$$

Для оценивания GLM удобно параметризовать данное распределение иначе:
$$ \mathbb{E}[x] = \frac{\lambda}{\alpha} = \mu,\hspace{15pt} Var(x) = \frac{\lambda}{\alpha^2} = \frac{\mu^2}{\lambda}.$$
Тогда,
$$f(x;\mu,\lambda) = \frac{1}{\Gamma(\lambda)}\alpha^\lambda x^{\lambda-1}e^{-\alpha x} = \frac{1}{\Gamma(\lambda)}\left(\frac{\lambda}{\mu}\right)^\lambda x^{\lambda-1}e^{-\left(\frac{\lambda}{\mu}\right)x} = \frac{1}{x\cdot\Gamma(\lambda)}\left(\frac{\lambda x}{\mu}\right)^\lambda e^{-\frac{\lambda x}{\mu}},\hspace{15pt} x\ge 0.$$

Также напомним, что для GLM с функцией связи $\ln(x)$ предсказание (оценка математического ожидания) имеет вид $\hat {y} = e^{x{^T}\beta + {\beta_{0}}}$.


Тогда, для оценивания коэффициентов нашей модели необходимо максимизировать правдоподобие (совместную условную вероятность при имеющихся данных), что данные имеют Гамма-распределение, в предположении известного параметра $\lambda$:
$$p(y_1,\dots,y_n|x_1,\dots,x_n;\beta_0,\beta) = \prod_{i=1}^{N}\frac{1}{y_i\cdot\Gamma(\lambda)}\left(\frac{\lambda y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}\right)^\lambda e^{-\frac{\lambda y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}} = L(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n).$$
Для упрощения задачи оптимизации перейдем к логарифму правдоподобия:
\begin{align}
\ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n) &= \sum_{i=1}^{N}\left(-\ln(\Gamma(\lambda))-\ln(y_i)+ \lambda\ln\left(\frac{\lambda y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}\right) -\frac{\lambda y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}\right)\\ &= \sum_{i=1}^{N}\left(-\ln(\Gamma(\lambda))-\ln(y_i) + \lambda\ln\left(\lambda\right)+\lambda\ln\left(y_i\right)-\lambda\left({x_i{^T}\beta + {\beta_{0}}}\right) -\frac{\lambda y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}\right)\\ &= \sum_{i=1}^{N}\left((\lambda-1)\ln\left(y_i\right)-\ln(\Gamma(\lambda)) + \lambda\ln\left(\lambda\right)-\lambda\left({x_i{^T}\beta + {\beta_{0}}}\right) -\frac{\lambda y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}\right).
\end{align}
Тогда обозначим слагаемые, не зависящие от параметров модели ($\beta_0$, $\beta$), как некоторую константу $C$, получаем:
$$\ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n) = \sum_{i=1}^{N}\left(-\lambda\left(\left({x_i{^T}\beta + {\beta_{0}}}\right) +\frac{y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}\right) + C(y_i, \lambda)\right),$$
Таким образом, требуется максимизировать
$$\ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n) = -\sum_{i=1}^{N}\left(\left({x_i{^T}\beta + {\beta_{0}}}\right) + \frac{y_i}{e^{x_i{^T}\beta + {\beta_{0}}}}\right),$$
Далее численно решается задача оптимизации для определения параметров модели:
$$\frac{\partial \ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n)}{\partial \beta_0} = 0,\\\frac{\partial \ell(\beta_0,\beta|y_1,\dots,y_n,x_1,\dots,x_n)}{\partial \beta} = 0.$$
Обычно минимизируется отрицательное правдоподобие, которое является выпуклой функцией.

##### Вывод метрики Deviance для GLM с Гамма-распределением

Метрика Deviance представляет собой отношение правдоподобия между двумя моделями: рассматриваемой моделью и "идеальной" моделью, в которая бы идеально предсказывала бы зависимую переменную.
$$Deviance = 2(\ell_{ideal} - \ell_{model})$$

В качестве такой "идеальной модели" может использоваться сама зависимая переменная. Тогда, логарифм правдоподобия "идеальной модели" для GLM с распределением Пуассона имеет вид:
$$\ell_{ideal} = -\sum_{i=1}^{N}\left(1 + \ln(y_i)\right).$$

Из приведенного выше вывода правдоподобия для рассматриваемой модели, мы можем записать, обозначив $\hat{y}_i = e^{x{^T}\beta + {\beta_{0}}}$:
$$\ell_{model} = -\sum_{i=1}^{N}\left(\frac{y_i}{\hat{y}_i} + \ln(\hat{y}_i)\right).$$

Тогда получаем,
$$Deviance = 2\sum_{i=1}^{N}\left(- 1 - \ln(y_i) + \frac{y_i}{\hat{y}_i} + \ln(\hat{y}_i)\right) = 2\sum_{i=1}^{N}\left(-\ln\left(\frac{y_i}{\hat{y}_i}\right)+\frac{y_i-\hat{y}_i}{\hat{y}_i} \right).$$

#### Дополнительная литература по GLM

*   [P. McCullagh, John A. Nelder _"Generalized Linear Models"_](http://www.utstat.toronto.edu/~brunner/oldclass/2201s11/readings/glmbook.pdf)
*   [D. Anderson, et al. _"A practitioner’s guide to generalized linear models"_](https://www.casact.org/pubs/dpp/dpp04/04dpp1.pdf)
*   [E. Ohlsson, B. Johansson _"Non-life insurance pricing with generalized linear models"_](https://www.springer.com/gp/book/9783642107900)
*   [P. De Jong, G. Heller _"Generalized linear models for insurance data"_](https://feb.kuleuven.be/public/u0017833/boek.pdf)




### Установка H2O на Google Colaboratory и инициализация

In [90]:
#!conda install -c cyclus java-jre

In [91]:
!java -version

openjdk version "1.8.0_121"
OpenJDK Runtime Environment (Zulu 8.20.0.5-win64) (build 1.8.0_121-b15)
OpenJDK 64-Bit Server VM (Zulu 8.20.0.5-win64) (build 25.121-b15, mixed mode)


In [92]:
# !conda install -c anaconda h2o

In [93]:
import h2o
from h2o.estimators.glm import H2OGeneralizedLinearEstimator
h2o.init()

Checking whether there is an H2O instance running at http://localhost:54321 . connected.


--------------------------  ---------------------------------------------------------
H2O cluster uptime:         48 mins 57 secs
H2O cluster timezone:       Europe/Moscow
H2O data parsing timezone:  UTC
H2O cluster version:        3.28.0.1
H2O cluster version age:    6 days
H2O cluster name:           H2O_from_python_ataga_9xz4ug
H2O cluster total nodes:    1
H2O cluster free memory:    3.035 Gb
H2O cluster total cores:    12
H2O cluster allowed cores:  12
H2O cluster status:         locked, healthy
H2O connection url:         http://localhost:54321
H2O connection proxy:       {'http': None, 'https': None}
H2O internal security:      False
H2O API Extensions:         Amazon S3, Algos, AutoML, Core V3, TargetEncoder, Core V4
Python version:             3.7.1 final
--------------------------  ---------------------------------------------------------

### Построение GLM для частоты страховых случаев

In [94]:
# Преобразование в H2O-Frame

h2o_train_c = h2o.H2OFrame(pd.concat([x_train_c, y_train_c], axis=1))
h2o_valid_c = h2o.H2OFrame(pd.concat([x_valid_c, y_valid_c], axis=1))
h2o_test_c = h2o.H2OFrame(pd.concat([x_test_c, y_test_c], axis=1))

Parse progress: |█████████████████████████████████████████████████████████| 100%
Parse progress: |█████████████████████████████████████████████████████████| 100%
Parse progress: |█████████████████████████████████████████████████████████| 100%


In [95]:
print(h2o_train_c.names)

['Exposure', 'LicAge', 'Gender', 'MariStat', 'DrivAge', 'HasKmLimit', 'BonusMalus', 'OutUseNb', 'RiskArea', 'VehUsg_Private', 'VehUsg_Private+trip to office', 'VehUsg_Professional', 'VehUsg_Professional run', 'CSP1', 'CSP2', 'CSP3', 'CSP4', 'CSP5', 'CSP6', 'CSP7', 'DrivAgeSq', 'ClaimsCount']


In [96]:
# Инициализируем и обучим GLM модель c кросс-валидацией

glm_poisson = H2OGeneralizedLinearEstimator(family = "poisson", link = "Log", nfolds=5)
glm_poisson.train(y="ClaimsCount", x = h2o_train_c.names[1:-1], \
                  training_frame = h2o_train_c, validation_frame = h2o_valid_c, weights_column = "Exposure")

glm Model Build progress: |███████████████████████████████████████████████| 100%


In [97]:
# Параметры модели: распределение, функция связи, гиперпараметры регуляризации, 
# количество использованных объясняющих переменных

glm_poisson.summary()


GLM Model: summary


family link                                 regularization  \
0    poisson  log  Elastic Net (alpha = 0.5, lambda = 1.308E-4 )   

   number_of_predictors_total number_of_active_predictors  \
0                          20                          19   

   number_of_iterations  \
0                     3   

                                           training_frame  
0  Key_Frame__upload_aa28bddaad90ee617af6cef1c6ef4b62.hex

In [98]:
# Метрики качества модели - по всем данным и на кросс-валидации

glm_poisson.cross_validation_metrics_summary().as_data_frame()

mean            sd   cv_1_valid  \
0                     mae   0.50276554  0.0051763733    0.4972649   
1  mean_residual_deviance    1.2432618    0.02396885    1.2108259   
2                     mse    0.7543464    0.02870083    0.7164619   
3           null_deviance     9371.959     178.93933     9212.751   
4                      r2  0.012211887  0.0020835875  0.011261137   
5       residual_deviance     9138.789     156.99974      8988.72   
6                    rmse    0.8684054   0.016524464   0.84644073   
7                   rmsle    0.4101862   0.003351727   0.40602922   

    cv_2_valid   cv_3_valid   cv_4_valid   cv_5_valid  
0    0.5003804    0.5097369   0.49988994    0.5065556  
1    1.2322443    1.2708367      1.24029    1.2621124  
2   0.74623394    0.7916594    0.7451986    0.7721779  
3     9373.829     9567.394     9174.297     9531.525  
4  0.011358874  0.015871437  0.011840551  0.010727436  
5     9153.425     9277.671     8968.889     9305.241  
6    0.8638483   0.88975245    0.8632489    0.8787365  
7   0.40856862    0.4141172   0.40912214   0.41309384

In [99]:
# Таблица коэффициентов модели (в зависимости от модели могут выводиться также стандартная ошибка, z-score и p-value)

glm_poisson._model_json['output']['coefficients_table'].as_data_frame()

names  coefficients  standardized_coefficients
0                       Intercept     -2.232571                  -1.289184
1                          LicAge      0.000046                   0.007411
2                          Gender     -0.020411                  -0.009888
3                        MariStat     -0.127848                  -0.045723
4                         DrivAge      0.006846                   0.102613
5                      HasKmLimit     -0.451913                  -0.139946
6                      BonusMalus      0.012746                   0.192535
7                        OutUseNb      0.095582                   0.064078
8                        RiskArea      0.013265                   0.029377
9                  VehUsg_Private     -0.232444                  -0.110219
10  VehUsg_Private+trip to office      0.000000                   0.000000
11            VehUsg_Professional      0.329256                   0.110543
12        VehUsg_Professional run      0.438860                   0.060281
13                           CSP1     -0.171310                  -0.026524
14                           CSP2     -0.355247                  -0.059985
15                           CSP3      0.348971                   0.035770
16                           CSP4      0.053866                   0.013629
17                           CSP5     -0.011842                  -0.005672
18                           CSP6      0.088620                   0.036884
19                           CSP7     -0.872463                  -0.010643
20                      DrivAgeSq     -0.000071                  -0.109886

In [100]:
# Таблица нормированных коэффициентов по всем данным и на кросс-валидации

pmodels = {}
pmodels['overall'] = glm_poisson.coef_norm()
for x in range(len(glm_poisson.cross_validation_models())):
    pmodels[x] = glm_poisson.cross_validation_models()[x].coef_norm()
pd.DataFrame.from_dict(pmodels).round(5)

overall        0        1        2        3  \
Intercept                     -1.28918 -1.28157 -1.28610 -1.29538 -1.28915   
LicAge                         0.00741  0.02091  0.05250 -0.01305  0.00000   
Gender                        -0.00989 -0.00245 -0.00790 -0.02041 -0.01103   
MariStat                      -0.04572 -0.04701 -0.04423 -0.04007 -0.03892   
DrivAge                        0.10261  0.11678  0.01927  0.01384  0.10145   
HasKmLimit                    -0.13995 -0.13575 -0.13975 -0.13436 -0.15138   
BonusMalus                     0.19253  0.20348  0.20284  0.18088  0.18391   
OutUseNb                       0.06408  0.06363  0.05928  0.06945  0.06574   
RiskArea                       0.02938  0.02672  0.04353  0.02590  0.01632   
VehUsg_Private                -0.11022 -0.12473 -0.09932 -0.09127 -0.10311   
VehUsg_Private+trip to office  0.00000  0.00000  0.00092  0.02172  0.00000   
VehUsg_Professional            0.11054  0.10118  0.11731  0.11400  0.11970   
VehUsg_Professional run        0.06028  0.05824  0.06532  0.06474  0.05887   
CSP1                          -0.02652 -0.02840 -0.03704 -0.02704 -0.04125   
CSP2                          -0.05998 -0.05082 -0.06313 -0.07679 -0.08506   
CSP3                           0.03577  0.02738  0.02542  0.04113  0.02732   
CSP4                           0.01363  0.01915  0.00134  0.00311  0.00335   
CSP5                          -0.00567 -0.01334 -0.01244 -0.01670 -0.03577   
CSP6                           0.03688  0.01731  0.03278  0.02401  0.00311   
CSP7                          -0.01064 -0.00934 -0.01230 -0.02851 -0.00813   
DrivAgeSq                     -0.10989 -0.10811 -0.06668 -0.00607 -0.10529   

                                     4  
Intercept                     -1.29544  
LicAge                        -0.00235  
Gender                        -0.00635  
MariStat                      -0.06174  
DrivAge                        0.11841  
HasKmLimit                    -0.13925  
BonusMalus                     0.18800  
OutUseNb                       0.06270  
RiskArea                       0.03544  
VehUsg_Private                -0.11015  
VehUsg_Private+trip to office  0.00000  
VehUsg_Professional            0.11762  
VehUsg_Professional run        0.06175  
CSP1                          -0.02321  
CSP2                          -0.05391  
CSP3                           0.04080  
CSP4                           0.00060  
CSP5                          -0.02411  
CSP6                           0.03145  
CSP7                          -0.01080  
DrivAgeSq                     -0.13231

In [101]:
# Построение прогнозных значений для обучающей, валидационной и тестовой выборок

c_train_pred = glm_poisson.predict(h2o_train_c).as_data_frame()
c_valid_pred = glm_poisson.predict(h2o_valid_c).as_data_frame()
c_test_pred = glm_poisson.predict(h2o_test_c).as_data_frame()

glm prediction progress: |████████████████████████████████████████████████| 100%
glm prediction progress: |████████████████████████████████████████████████| 100%
glm prediction progress: |████████████████████████████████████████████████| 100%


### Построение GLM для среднего убытка

In [102]:
# Преобразование в H2O-Frame

h2o_train_ac = h2o.H2OFrame(pd.concat([x_train_ac, y_train_ac], axis=1))
h2o_valid_ac = h2o.H2OFrame(pd.concat([x_valid_ac, y_valid_ac], axis=1))
h2o_test_ac = h2o.H2OFrame(pd.concat([x_test_ac, y_test_ac], axis=1))

Parse progress: |█████████████████████████████████████████████████████████| 100%
Parse progress: |█████████████████████████████████████████████████████████| 100%
Parse progress: |█████████████████████████████████████████████████████████| 100%


In [103]:
print(h2o_train_ac.names)

['Exposure', 'LicAge', 'Gender', 'MariStat', 'DrivAge', 'HasKmLimit', 'BonusMalus', 'OutUseNb', 'RiskArea', 'VehUsg_Private', 'VehUsg_Private+trip to office', 'VehUsg_Professional', 'VehUsg_Professional run', 'CSP1', 'CSP2', 'CSP3', 'CSP4', 'CSP5', 'CSP6', 'CSP7', 'DrivAgeSq', 'AvgClaim']


In [104]:
# Инициализируем и обучим GLM модель c кросс-валидацией

glm_gamma = H2OGeneralizedLinearEstimator(family = "gamma", link = "Log", nfolds=5)
glm_gamma.train(y="AvgClaim", x = h2o_train_ac.names[1:-1], training_frame = h2o_train_ac, validation_frame = h2o_valid_ac, weights_column = "Exposure")

glm Model Build progress: |███████████████████████████████████████████████| 100%


In [105]:
# Параметры модели: распределение, функция связи, гиперпараметры регуляризации, 
# количество использованных объясняющих переменных

glm_gamma.summary()


GLM Model: summary


family link                                 regularization  \
0    gamma  log  Elastic Net (alpha = 0.5, lambda = 1.782E-4 )   

   number_of_predictors_total number_of_active_predictors  \
0                          20                          19   

   number_of_iterations  \
0                     3   

                                           training_frame  
0  Key_Frame__upload_b7b0e169ef2984952bb3c8d031d94299.hex

In [106]:
# Метрики качества модели - по всем данным и на кросс-валидации

glm_gamma.cross_validation_metrics_summary().as_data_frame()

mean           sd    cv_1_valid  \
0                     mae     1046.0056     40.70445    1023.78796   
1  mean_residual_deviance     1.9558129   0.07643206     1.8824772   
2                     mse     7412848.0    5690569.0     5099994.0   
3           null_deviance     1854.3999    34.405724     1801.9069   
4                      r2  -5.690317E-4  0.006229699  0.0036878742   
5       residual_deviance     1847.4296    43.890274     1783.6207   
6                    rmse      2590.327     937.4528     2258.3167   
7                   rmsle     1.7109987  0.027994268      1.673061   

     cv_2_valid   cv_3_valid     cv_4_valid    cv_5_valid  
0     1029.9857    1063.1211     1004.79254      1108.341  
1     1.9738233    1.9597309      1.8911612      2.071872  
2     4237704.0    7427862.0      3109366.8   1.7189314E7  
3      1874.266    1890.8221      1863.7063     1841.2983  
4  -0.006801764  0.006531816  -0.0072976826  0.0010345975  
5     1898.4963    1856.9567      1870.6023      1827.472  
6     2058.5686    2725.4104      1763.3396     4145.9995  
7     1.7277392    1.6929327      1.7432404     1.7180197

In [107]:
# Таблица коэффициентов модели (в зависимости от модели могут выводиться также стандартная ошибка, z-score и p-value)

glm_gamma._model_json['output']['coefficients_table'].as_data_frame()

names  coefficients  standardized_coefficients
0                       Intercept      7.622904                   6.920750
1                          LicAge     -0.000346                  -0.054870
2                          Gender     -0.053660                  -0.025964
3                        MariStat      0.150567                   0.055406
4                         DrivAge     -0.035689                  -0.524162
5                      HasKmLimit     -0.055473                  -0.013748
6                      BonusMalus     -0.002959                  -0.048894
7                        OutUseNb      0.014387                   0.010521
8                        RiskArea      0.042049                   0.094112
9                  VehUsg_Private      0.040138                   0.018185
10  VehUsg_Private+trip to office      0.000000                   0.000000
11            VehUsg_Professional     -0.037911                  -0.013968
12        VehUsg_Professional run     -0.246361                  -0.037118
13                           CSP1      0.116052                   0.017820
14                           CSP2     -0.121922                  -0.020516
15                           CSP3     -0.165770                  -0.017081
16                           CSP4     -0.042381                  -0.011751
17                           CSP5      0.051988                   0.024517
18                           CSP6     -0.005362                  -0.002085
19                           CSP7     -1.365733                  -0.015087
20                      DrivAgeSq      0.000371                   0.547532

In [108]:
# Таблица нормированных коэффициентов по всем данным и на кросс-валидации

pmodels = {}
pmodels['overall'] = glm_gamma.coef_norm()
for x in range(len(glm_gamma.cross_validation_models())):
    pmodels[x] = glm_gamma.cross_validation_models()[x].coef_norm()
pd.DataFrame.from_dict(pmodels).round(5)

overall        0        1        2        3  \
Intercept                      6.92075  6.92094  6.91992  6.92169  6.93201   
LicAge                        -0.05487 -0.01403 -0.06364 -0.04357 -0.14796   
Gender                        -0.02596 -0.04901 -0.00708 -0.03480 -0.02737   
MariStat                       0.05541  0.05648  0.07607  0.04715  0.07303   
DrivAge                       -0.52416 -0.49923 -0.71623 -0.49153 -0.34017   
HasKmLimit                    -0.01375 -0.02073 -0.01820 -0.01332 -0.00100   
BonusMalus                    -0.04889 -0.05231 -0.07147 -0.03922 -0.03954   
OutUseNb                       0.01052 -0.00757  0.01822  0.02993  0.00570   
RiskArea                       0.09411  0.08605  0.10273  0.07022  0.10145   
VehUsg_Private                 0.01818  0.03569  0.02691  0.00435 -0.00428   
VehUsg_Private+trip to office  0.00000  0.00000 -0.00305  0.00000  0.01075   
VehUsg_Professional           -0.01397 -0.04357  0.00000 -0.01207  0.00000   
VehUsg_Professional run       -0.03712 -0.04147 -0.02664 -0.03962 -0.03470   
CSP1                           0.01782  0.02714  0.01956 -0.00006  0.01849   
CSP2                          -0.02052 -0.01373 -0.01491 -0.04475 -0.02081   
CSP3                          -0.01708 -0.01531 -0.01632 -0.02682 -0.01486   
CSP4                          -0.01175  0.00000  0.00000 -0.02145 -0.02223   
CSP5                           0.02452  0.01469  0.06105  0.00388  0.00000   
CSP6                          -0.00209 -0.03392 -0.01178  0.00000  0.00139   
CSP7                          -0.01509  0.00000 -0.01696 -0.01799 -0.01727   
DrivAgeSq                      0.54753  0.49851  0.76083  0.51406  0.43792   

                                     4  
Intercept                      6.90362  
LicAge                        -0.00772  
Gender                        -0.01171  
MariStat                       0.02061  
DrivAge                       -0.58853  
HasKmLimit                    -0.01417  
BonusMalus                    -0.04389  
OutUseNb                       0.00777  
RiskArea                       0.10872  
VehUsg_Private                 0.03097  
VehUsg_Private+trip to office  0.00000  
VehUsg_Professional           -0.00958  
VehUsg_Professional run       -0.04233  
CSP1                           0.01226  
CSP2                          -0.02619  
CSP3                          -0.01995  
CSP4                          -0.03731  
CSP5                           0.00144  
CSP6                           0.00000  
CSP7                          -0.01670  
DrivAgeSq                      0.54311

In [109]:
# Построение прогнозных значений для обучающей, валидационной и тестовой выборок

ac_train_pred = glm_gamma.predict(h2o_train_ac).as_data_frame()
ac_valid_pred = glm_gamma.predict(h2o_valid_ac).as_data_frame()
ac_test_pred = glm_gamma.predict(h2o_test_ac).as_data_frame()

glm prediction progress: |████████████████████████████████████████████████| 100%
glm prediction progress: |████████████████████████████████████████████████| 100%
glm prediction progress: |████████████████████████████████████████████████| 100%


### Использование GLM моделей

In [110]:
h2o_df = h2o.H2OFrame(df)

Parse progress: |█████████████████████████████████████████████████████████| 100%


In [111]:
df['CountPredicted'] = glm_poisson.predict(h2o_df).as_data_frame()
df['AvgClaimPredicted'] = glm_gamma.predict(h2o_df).as_data_frame()

glm prediction progress: |████████████████████████████████████████████████| 100%
glm prediction progress: |████████████████████████████████████████████████| 100%


In [112]:
df['BurningCost'] = df.CountPredicted * df.AvgClaimPredicted
df[['CountPredicted', 'AvgClaimPredicted', 'BurningCost']].head()

CountPredicted  AvgClaimPredicted  BurningCost
0        0.375992         988.222409   371.563352
1        0.376009         987.880713   371.452138
2        0.322919        1039.015533   335.517481
3        0.261780         926.138283   242.444676
4        0.230704         923.064855   212.954902

## * Домашнее задание: GLM для прогнозирования наступления страхового случая

In [113]:
# Разбиение датасета на train/val/test

x_train_ind, x_test_ind, y_train_ind, y_test_ind = train_test_split(
    df.drop(
        ['ClaimInd', 'ClaimAmount', 'ClaimsCount', 'CountPredicted', 'AvgClaimPredicted', 'BurningCost'], axis=1
    ), df.ClaimInd, test_size=0.15, random_state=1)
x_train_ind, x_valid_ind, y_train_ind, y_valid_ind = train_test_split(
    x_train_ind, y_train_ind, test_size=0.15, random_state=1)

In [114]:
# Преобразование в H2O-Frame

h2o_train_ind = h2o.H2OFrame(pd.concat([x_train_ind, y_train_ind], axis=1))
h2o_valid_ind = h2o.H2OFrame(pd.concat([x_valid_ind, y_valid_ind], axis=1))
h2o_test_ind = h2o.H2OFrame(pd.concat([x_test_ind, y_test_ind], axis=1))

Parse progress: |█████████████████████████████████████████████████████████| 100%
Parse progress: |█████████████████████████████████████████████████████████| 100%
Parse progress: |█████████████████████████████████████████████████████████| 100%


In [115]:
# Преобразуем целевую переменную ClaimInd в категориальную при помощи метода asfactor во всех наборах данных

h2o_train_ind['ClaimInd'] = h2o_train_ind['ClaimInd'].asfactor()
h2o_valid_ind['ClaimInd'] = h2o_valid_ind['ClaimInd'].asfactor()
h2o_test_ind['ClaimInd'] = h2o_test_ind['ClaimInd'].asfactor()

In [126]:
# Инициализируем и обучим GLM модель c кросс-валидацией

glm = H2OGeneralizedLinearEstimator(family = "binomial", link = "Logit", nfolds=5)
glm.train(y="ClaimInd", x=h2o_train_ind.names[1:-1], \
                  training_frame=h2o_train_ind, validation_frame=h2o_valid_ind, weights_column = "Exposure")

glm Model Build progress: |███████████████████████████████████████████████| 100%


In [127]:
# Параметры модели: распределение, функция связи, гиперпараметры регуляризации, 
# количество использованных объясняющих переменных

glm.summary()


GLM Model: summary


family   link                                 regularization  \
0    binomial  logit  Elastic Net (alpha = 0.5, lambda = 3.226E-5 )   

   number_of_predictors_total number_of_active_predictors  \
0                          20                          20   

   number_of_iterations training_frame  
0                     3  py_4_sid_9e76

In [128]:
# Метрики качества модели - по всем данным и на кросс-валидации

glm.cross_validation_metrics_summary().as_data_frame()

mean            sd   cv_1_valid  \
0                  accuracy   0.44824797    0.13502568    0.4256374   
1                       auc   0.57025445  0.0073462795   0.57725006   
2                     aucpr   0.15600158   0.005774732   0.16278702   
3                       err   0.55175203    0.13502568   0.57436264   
4                 err_count      4055.08      991.6142      4213.72   
5                  f0point5   0.17526704   0.007789099   0.17960514   
6                        f1   0.24115224   0.005751531   0.25042516   
7                        f2   0.39039978   0.038505364   0.41345397   
8            lift_top_group          0.0           0.0          0.0   
9                   logloss   0.37893492  0.0064802216   0.38493192   
10      max_per_class_error    0.6288654    0.12264272    0.6204569   
11                      mcc   0.07056884  0.0088578835   0.07719653   
12  mean_per_class_accuracy   0.54922533   0.009677187    0.5550171   
13     mean_per_class_error   0.45077467   0.009677187   0.44498292   
14                      mse  0.110771134   0.002497758   0.11321005   
15            null_deviance    5620.4756     112.93706    5707.9053   
16                   pr_auc   0.15600158   0.005774732   0.16278702   
17                precision   0.14840174   0.009162222   0.15111502   
18                       r2  0.006365023   0.002035587  0.007725008   
19                   recall   0.68551016    0.16434543   0.73049104   
20        residual_deviance    5571.4526     110.43389    5647.9834   
21                     rmse   0.33280605   0.003752237   0.33646703   
22              specificity    0.4129405    0.17954065   0.37954313   

      cv_2_valid   cv_3_valid   cv_4_valid   cv_5_valid  
0     0.28547376   0.37284157    0.5228361     0.634451  
1      0.5630556    0.5785116    0.5635352    0.5689199  
2     0.15554252   0.15945265    0.1474096   0.15481614  
3     0.71452624    0.6271584    0.4771639   0.36554906  
4       5260.888     4613.003     3477.968     2709.822  
5     0.16863208   0.16900152   0.17233977   0.18675672  
6     0.24163991    0.2394364   0.23480688   0.23945282  
7     0.42612883    0.4105357   0.36830422   0.33357617  
8            0.0          0.0          0.0          0.0  
9     0.38623866   0.37404075   0.37161908   0.37784415  
10     0.8024504    0.6863918   0.48705956   0.54796845  
11   0.056407485   0.07061377   0.06976701   0.07885939  
12    0.53270686    0.5488318   0.55302453    0.5565464  
13    0.46729317   0.45116815   0.44697547   0.44345364  
14    0.11341876   0.10908009   0.10777481  0.110371955  
15     5723.5117    5568.9297     5449.891    5652.1396  
16    0.15554252   0.15945265    0.1474096   0.15481614  
17    0.14036025   0.14129226   0.14637846    0.1628627  
18  0.0047787097  0.008863557  0.003928078  0.006529763  
19     0.8678641    0.7840554   0.59310865   0.45203158  
20     5687.5684     5502.441     5417.339     5601.932  
21      0.336777   0.33027276   0.32829073   0.33222276  
22     0.1975496   0.31360826    0.5129404   0.66106117

In [129]:
# Таблица коэффициентов модели (в зависимости от модели могут выводиться также стандартная ошибка, z-score и p-value)

glm._model_json['output']['coefficients_table'].as_data_frame()

names  coefficients  standardized_coefficients
0                       Intercept     -2.281283                  -1.945709
1                          LicAge     -0.000124                  -0.019844
2                          Gender     -0.006755                  -0.003273
3                        MariStat     -0.059439                  -0.021257
4                         DrivAge     -0.004067                  -0.060961
5                      HasKmLimit     -0.412808                  -0.127837
6                      BonusMalus      0.006568                   0.099217
7                        OutUseNb      0.087129                   0.058411
8                        RiskArea      0.008654                   0.019165
9                  VehUsg_Private     -0.156076                  -0.074007
10  VehUsg_Private+trip to office     -0.004492                  -0.002246
11            VehUsg_Professional      0.275953                   0.092647
12        VehUsg_Professional run      0.290163                   0.039857
13                           CSP1     -0.059433                  -0.009202
14                           CSP2     -0.141911                  -0.023962
15                           CSP3      0.404095                   0.041420
16                           CSP4      0.170530                   0.043145
17                           CSP5      0.118444                   0.056727
18                           CSP6      0.201156                   0.083723
19                           CSP7     -0.513237                  -0.006261
20                      DrivAgeSq      0.000015                   0.023576

In [130]:
# Таблица нормированных коэффициентов по всем данным и на кросс-валидации

pmodels = {}
pmodels['overall'] = glm.coef_norm()
for x in range(len(glm.cross_validation_models())):
    pmodels[x] = glm.cross_validation_models()[x].coef_norm()
pd.DataFrame.from_dict(pmodels).round(5)

overall        0        1        2        3  \
Intercept                     -1.94571 -1.95315 -1.95503 -1.93924 -1.93808   
LicAge                        -0.01984 -0.02737 -0.00825  0.00869 -0.01602   
Gender                        -0.00327  0.00056  0.00601 -0.01930 -0.00536   
MariStat                      -0.02126 -0.01720 -0.03600 -0.01599 -0.01159   
DrivAge                       -0.06096 -0.01479 -0.07024 -0.06673 -0.09331   
HasKmLimit                    -0.12784 -0.13504 -0.12062 -0.11340 -0.13678   
BonusMalus                     0.09922  0.10632  0.08874  0.09780  0.10566   
OutUseNb                       0.05841  0.06084  0.07132  0.04949  0.05717   
RiskArea                       0.01917  0.01034  0.02609  0.02165  0.01741   
VehUsg_Private                -0.07401 -0.07254 -0.09885 -0.07141 -0.08930   
VehUsg_Private+trip to office -0.00225  0.00000 -0.00368 -0.01114 -0.01211   
VehUsg_Professional            0.09265  0.08525  0.07550  0.09510  0.09347   
VehUsg_Professional run        0.03986  0.04158  0.04071  0.03596  0.03750   
CSP1                          -0.00920 -0.02306 -0.02416 -0.02288 -0.02626   
CSP2                          -0.02396 -0.04008 -0.03014 -0.05892 -0.04432   
CSP3                           0.04142  0.03006  0.03260  0.02518  0.03333   
CSP4                           0.04315  0.01650  0.01668  0.00543  0.02290   
CSP5                           0.05673 -0.00048 -0.00346  0.00000  0.01911   
CSP6                           0.08372  0.03597  0.03367  0.03901  0.04948   
CSP7                          -0.00626 -0.00401 -0.04383 -0.00467  0.00012   
DrivAgeSq                      0.02358  0.00000  0.01285 -0.00556  0.06422   

                                     4  
Intercept                     -1.94486  
LicAge                        -0.06397  
Gender                         0.00053  
MariStat                      -0.02409  
DrivAge                       -0.01035  
HasKmLimit                    -0.13335  
BonusMalus                     0.09888  
OutUseNb                       0.05282  
RiskArea                       0.01986  
VehUsg_Private                -0.07418  
VehUsg_Private+trip to office -0.02310  
VehUsg_Professional            0.08758  
VehUsg_Professional run        0.03239  
CSP1                          -0.02120  
CSP2                          -0.02500  
CSP3                           0.03833  
CSP4                           0.03780  
CSP5                           0.04917  
CSP6                           0.07092  
CSP7                          -0.00670  
DrivAgeSq                      0.00314

In [131]:
# Построение прогнозных значений для обучающей, валидационной и тестовой выборок

train_pred = glm.predict(h2o_train_ind).as_data_frame()
valid_pred = glm.predict(h2o_valid_ind).as_data_frame()
test_pred = glm.predict(h2o_test_ind).as_data_frame()

glm prediction progress: |████████████████████████████████████████████████| 100%
glm prediction progress: |████████████████████████████████████████████████| 100%
glm prediction progress: |████████████████████████████████████████████████| 100%


In [132]:
from sklearn.metrics import accuracy_score, f1_score, confusion_matrix

In [133]:
# Выведем импортированные выше метрики классификации для обучающей, валидационной и тестовой выборок

acc_train = accuracy_score(y_train_ind, train_pred.iloc[:, :1])
acc_train

0.31679848073270994

In [134]:
acc_valid = accuracy_score(y_valid_ind, valid_pred.iloc[:, :1])
acc_valid

0.3183273173057277

In [135]:
acc_test = accuracy_score(y_test_ind, test_pred.iloc[:, :1])
acc_test

0.3135347921732083

In [136]:
f1_train = f1_score(y_train_ind, train_pred.iloc[:, :1])
f1_train

0.1828375911097054

In [137]:
f1_valid = f1_score(y_valid_ind, valid_pred.iloc[:, :1])
f1_valid

0.18380494169452827

In [138]:
f1_test = f1_score(y_test_ind, test_pred.iloc[:, :1])
f1_test

0.18051140290255702

In [139]:
matrix_train = confusion_matrix(y_train_ind, train_pred.iloc[:, :1])
matrix_train

array([[19998, 55351],
       [ 1490,  6359]], dtype=int64)

In [140]:
matrix_valid = confusion_matrix(y_valid_ind, valid_pred.iloc[:, :1])
matrix_valid

array([[3547, 9730],
       [ 279, 1127]], dtype=int64)

In [141]:
matrix_test = confusion_matrix(y_test_ind, test_pred.iloc[:, :1])
matrix_test

array([[ 4110, 11550],
       [  308,  1306]], dtype=int64)

Какие проблемы вы здесь видите? Как можно улучшить данный результат?

Результаты плохие, возможно, не хватило времени вникнуть